In [5]:
import numpy as np
import math
import random
class Node:
    def __init__(self,numtheta):
        self.theta=[0.0]*numtheta
        self.downstream=None
        self.upstream=None
        self.output=None
        self.deljthetabydelthetaunit = [0.0]*numtheta
        self.deljthetabydelnet = None
def loadtheta(network,theta ):
    for i in range(len(network)):
        for j in range(len(network[i])):
            for k in range(len(network[i][j].theta)):
                network[i][j].theta[k] = theta[i][j][k]
    return network
def sigmoid(x):
    return (1.0/(1.0+math.exp(-x)))
def forwardpass(features, network):
    for i in range(len(network)):
        for j in range(len(network[i])):
            tempnode = network[i][j]
            temp=0.0
            if(i==0):
                #parse from input
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * features[k]
                
            else:
                #parse from last layer
                prevlayer = network[i-1]
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * prevlayer[k].output
            tempnode.output = sigmoid(temp)
    lastlayer = network[len(network)-1]
    templist=[]
    for i in range(len(lastlayer)):
        templist.append(lastlayer[i].output)
    return templist
def findcost(output, correctoutput):
    temp = 0.0
    for i in range(len(output)):
        temp += 0.5 * ((output[i]-correctoutput[i])**2)
    return temp
def findtotalcostarr(inparr,outarr,network):
    costarr=[]
    for i in range(len(inparr)):
        tempforwardpass= forwardpass(inparr[i],network)
        print("tempforwardpass is")
        print(tempforwardpass)
        tempcost = findcost(tempforwardpass,outarr[i])
        costarr.append(tempcost)
    avgcost=0.0
    for i in range(len(costarr)):
        avgcost += costarr[i]
    avgcost = avgcost/(len(costarr))
    return costarr, avgcost
def printdeljtheta(network):
    print("deljtheta is")
    templist=[]
    for i in range(len(network)):
        templist.append([])
        for j in range(len(network[i])):
            templist[i].append([])
            for k in range(len(network[i][j].theta)):
                templist[i][j].append(network[i][j].deljthetabydelthetaunit[k])
    print(templist)
    return
def neuralnet(inparr, outarr, hiddeninfo,learningrate, epochsize,costthres, sampletheta):
    numtrain = len(inparr)
    diminput= len(inparr[0])
    dimoutput = len(outarr[0])
    network=[]
    for i in range(len(hiddeninfo)):
        network.append([])
    network.append([])
    for i in range(len(hiddeninfo)):
        #i is layer iterator
        for j in range(hiddeninfo[i]):
            #j is sublayer num unit iterator
            if(i==0):
                tempnode = Node(diminput+1)
                network[i].append(tempnode)
            else:
                tempnode = Node(hiddeninfo[i-1]+1)
                network[i].append(tempnode)
            
    #add output layer
    for i in range(dimoutput):
        tempnode = Node(hiddeninfo[len(hiddeninfo)-1] + 1)
        network[len(network)-1].append(tempnode)
    #load theta for testing
#     network = loadtheta(network, sampletheta)
    #necessary forwardpass
#     tempforwardpass = forwardpass(inparr[0],network)
#     print(tempforwardpass)
#     #lets see cost
#     print("cost = "+str(findcost(tempforwardpass,outarr[0])))
    
    #time for backprop
    deljthetabydelthetamat=[]
    for i in range(len(network)):
        deljthetabydelthetamat.append([])
        for j in range(len(network[i])):
            deljthetabydelthetamat[i].append([])
            for k in range(len(network[i][j].theta)):
                deljthetabydelthetamat[i][j].append(0.0)
    print("simulated deljtheata")
    print(deljthetabydelthetamat)
    print("real deljtheta")
    printdeljtheta(network)
    subepochiter=0
    epochcount=0
    numwholedatapass=0
    numiter=0
    costarr,oldavgcost = findtotalcostarr(inparr,outarr,network)
    shufflehelper = []
    for i in range(len(inparr)):
    	shufflehelper.append(i)
    while(0==0):
        numiter+=1
        print("numiter is")
        print(numiter)
        print("numwholedata pass is")
        print(numwholedatapass)
        ioindex = epochsize*epochcount+subepochiter
        print("ioindex is "+str(ioindex))
        tempforwardpass = forwardpass(inparr[shufflehelper[ioindex]],network)
        for i in range(len(network)-1,-1,-1):
            #lets calculate deljtheta by del netj
            for j in range(len(network[i])):
                tempnode = network[i][j]
                if(i==len(network)-1):
                    tempnode.deljthetabydelnet = -1.0*(outarr[shufflehelper[ioindex]][j]-tempnode.output)*(tempnode.output)*(1.0-tempnode.output)
                else:
                    temp=0.0
                    nextlayer = network[i+1]
                    for k in range(len(nextlayer)):
                        temp += nextlayer[k].deljthetabydelnet * nextlayer[k].theta[j]
                    tempnode.deljthetabydelnet = (tempnode.output) * (1.0- tempnode.output) * temp
                if(i==0):
                    #ok is input
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * inparr[shufflehelper[ioindex]][k]
                else:
                    prevlayer = network[i-1]
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * prevlayer[k].output
        subepochiter+=1
        for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        deljthetabydelthetamat[i][j][k] += network[i][j].deljthetabydelthetaunit[k]
        print("simulated deljtheata")
        print(deljthetabydelthetamat)
        print("real deljtheta")
        printdeljtheta(network)
        if(subepochiter==epochsize):
            print("epoch over")
            for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        network[i][j].theta[k] = network[i][j].theta[k] - learningrate * deljthetabydelthetamat[i][j][k]/(1.0*epochsize)
                        deljthetabydelthetamat[i][j][k]=0.0
            #set deljthetabydel zero
            
            costarr, newavgcost=findtotalcostarr(inparr,outarr,network)
            print("cost is")
            print(newavgcost)
            if(newavgcost<costthres):
                print("cost is lower")
                break
            elif(numwholedatapass>=20000):
                break
            else:
                oldavgcost=newavgcost
                subepochiter=0
                epochcount+=1
                if(len(inparr)==epochcount*epochsize):
                    numwholedatapass+=1
                    epochcount=0
                    random.shuffle(shufflehelper)
        
            
            
            
#         tempforwardpass = forwardpass(inparr[0],network)
#         print(tempforwardpass)
#         #lets see cost
#         print("cost = "+str(findcost(tempforwardpass,outarr[0])))        
    
    return network
# sampleinparr = [[0.05, 0.10]]
sampleinparr = [[0.0, 1.0],[1.0,0.0],[0.0,0.0],[1.0,1.0]]

# sampleoutput = [[0.01, 0.99]]
sampleoutput = [[0.99],[0.99],[0.01],[0.99]]
samplehiddeninfo = [2]
samplelearningrate=1.0
sampletheta = [[[.15,.20,.35],[.25,.30,.35]],[[.40,.45,.60],[.50,.55,.60]]]

samplenetwork = neuralnet(sampleinparr,sampleoutput,samplehiddeninfo,samplelearningrate,1, pow(10,-4),sampletheta)
print(samplenetwork)
            
                
    
    

simulated deljtheata
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[0.0, 0.0, 0.0]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[0.0, 0.0, 0.0]]]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
numiter is
1
numwholedata pass is
0
ioindex is 0
simulated deljtheata
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[-0.06125, -0.06125, -0.1225]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0], [0.0, 0.0, 0.0]], [[-0.06125, -0.06125, -0.1225]]]
epoch over
tempforwardpass is
[0.5458086818730948]
tempforwardpass is
[0.5458086818730948]
tempforwardpass is
[0.5458086818730948]
tempforwardpass is
[0.5458086818730948]
cost is
0.10987609060856697
numiter is
2
numwholedata pass is
0
ioindex is 1
simulated deljtheata
[[[-0.0016861470049813246, 0.0, -0.0016861470049813246], [-0.0016861470049813246, 0.0, -0.0016861470049813246]], [[-0.055057861387145295, -0.055057861387145295, -0.11011572277429059]]]
real deljtheta
deljtheta is
[[[-0.0016861470049

epoch over
tempforwardpass is
[0.7218095796764981]
tempforwardpass is
[0.721637382737147]
tempforwardpass is
[0.7167544371588257]
tempforwardpass is
[0.7265948770085741]
cost is
0.08910358614491024
numiter is
75
numwholedata pass is
18
ioindex is 2
simulated deljtheata
[[[-0.004430455667018447, -0.004430455667018447, -0.004430455667018447], [-0.004430455667018447, -0.004430455667018447, -0.004430455667018447]], [[-0.029662667115589698, -0.029662667115589698, -0.05232668194196877]]]
real deljtheta
deljtheta is
[[[-0.004430455667018447, -0.004430455667018447, -0.004430455667018447], [-0.004430455667018447, -0.004430455667018447, -0.004430455667018447]], [[-0.029662667115589698, -0.029662667115589698, -0.05232668194196877]]]
epoch over
tempforwardpass is
[0.7386576377455527]
tempforwardpass is
[0.7384779521878195]
tempforwardpass is
[0.7332140250855242]
tempforwardpass is
[0.7437998962067194]
cost is
0.08876116759843825
numiter is
76
numwholedata pass is
18
ioindex is 3
simulated deljthea

numwholedata pass is
34
ioindex is 3
simulated deljtheata
[[[0.0, 0.0, 0.018339732694278986], [0.0, 0.0, 0.018339732694278986]], [[0.06514110259740576, 0.06514110259740576, 0.1322802908435145]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.018339732694278986], [0.0, 0.0, 0.018339732694278986]], [[0.06514110259740576, 0.06514110259740576, 0.1322802908435145]]]
epoch over
tempforwardpass is
[0.7564226285282787]
tempforwardpass is
[0.7563331288782925]
tempforwardpass is
[0.7429591444085725]
tempforwardpass is
[0.7688707855176715]
cost is
0.08691072899914568
numiter is
141
numwholedata pass is
35
ioindex is 0
simulated deljtheata
[[[-0.005192911660212285, 0.0, -0.005192911660212285], [-0.005192911660212285, 0.0, -0.005192911660212285]], [[-0.02414378043709511, -0.02414378043709511, -0.04306324509792128]]]
real deljtheta
deljtheta is
[[[-0.005192911660212285, -0.0, -0.005192911660212285], [-0.005192911660212285, -0.0, -0.005192911660212285]], [[-0.02414378043709511, -0.02414378043709511, -0.0

epoch over
tempforwardpass is
[0.800685378092398]
tempforwardpass is
[0.8006540366415861]
tempforwardpass is
[0.7711857408407121]
tempforwardpass is
[0.8249874386334983]
cost is
0.08479059967201266
numiter is
212
numwholedata pass is
52
ioindex is 3
simulated deljtheata
[[[0.0, 0.0, 0.024431417654297242], [0.0, 0.0, 0.024431417654297242]], [[0.06396319739893444, 0.06396319739893444, 0.13431753721898865]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.024431417654297242], [0.0, 0.0, 0.024431417654297242]], [[0.06396319739893444, 0.06396319739893444, 0.13431753721898865]]]
epoch over
tempforwardpass is
[0.7635253426290419]
tempforwardpass is
[0.763492846044825]
tempforwardpass is
[0.7333484767792583]
tempforwardpass is
[0.7890266159547811]
cost is
0.08327744764720331
numiter is
213
numwholedata pass is
53
ioindex is 0
simulated deljtheata
[[[0.0, -0.006577030045379764, -0.006577030045379764], [0.0, -0.006577030045379764, -0.006577030045379764]], [[-0.024154036260994147, -0.02415403626099414

cost is
0.07653109945068033
numiter is
283
numwholedata pass is
70
ioindex is 2
simulated deljtheata
[[[-0.010119924945334478, 0.0, -0.010119924945334478], [-0.010119924945334478, 0.0, -0.010119924945334478]], [[-0.03032222311652302, -0.03032222311652302, -0.04972040946961735]]]
real deljtheta
deljtheta is
[[[-0.010119924945334478, -0.0, -0.010119924945334478], [-0.010119924945334478, -0.0, -0.010119924945334478]], [[-0.03032222311652302, -0.03032222311652302, -0.04972040946961735]]]
epoch over
tempforwardpass is
[0.7530053252210327]
tempforwardpass is
[0.752966397990666]
tempforwardpass is
[0.6903066011066594]
tempforwardpass is
[0.7992946546055762]
cost is
0.07644212557830121
numiter is
284
numwholedata pass is
70
ioindex is 3
simulated deljtheata
[[[-0.00486301058581408, -0.00486301058581408, -0.00486301058581408], [-0.00486301058581408, -0.00486301058581408, -0.00486301058581408]], [[-0.023422369880247748, -0.023422369880247748, -0.030593468267125647]]]
real deljtheta
deljtheta is


...

ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.00042847995033904373], [0.0, 0.0, 0.00042847995033904373]], [[9.701053801297427e-05, 9.701053801297427e-05, 0.0007893161037867166]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.00042847995033904373], [0.0, 0.0, 0.00042847995033904373]], [[9.701053801297427e-05, 9.701053801297427e-05, 0.0007893161037867166]]]
epoch over
tempforwardpass is
[0.9783646638497788]
tempforwardpass is
[0.9783500249591908]
tempforwardpass is
[0.033977212914623973]
tempforwardpass is
[0.9956387507219612]
cost is
0.00010972565182971872
numiter is
6663
numwholedata pass is
1665
ioindex is 2
simulated deljtheata
[[[-0.00017234203881684823, 0.0, -0.00017234203881684823], [-0.00017234203881684823, 0.0, -0.00017234203881684823]], [[-0.00020570627210580748, -0.00020570627210580748, -0.00024676107602400926]]]
real deljtheta
deljtheta is
[[[-0.00017234203881684823, -0.0, -0.00017234203881684823], [-0.00017234203881684823, -0.0, -0.00017234203881684823]], [[-0.00020570627210

deljtheta is
[[[6.756596794036552e-07, 6.756596794036552e-07, 6.756596794036552e-07], [6.756596794036552e-07, 6.756596794036552e-07, 6.756596794036552e-07]], [[2.4312823947488658e-05, 2.4312823947488658e-05, 2.4447561193354074e-05]]]
epoch over
tempforwardpass is
[0.9785149935685136]
tempforwardpass is
[0.9785058110396468]
tempforwardpass is
[0.03373603360199481]
tempforwardpass is
[0.9956675689286757]
cost is
0.00010744279766298817
numiter is
6758
numwholedata pass is
1689
ioindex is 1
simulated deljtheata
[[[-0.0001688058439712468, 0.0, -0.0001688058439712468], [-0.0001688058439712468, 0.0, -0.0001688058439712468]], [[-0.00020160485068862791, -0.00020160485068862791, -0.00024174795233184815]]]
real deljtheta
deljtheta is
[[[-0.0001688058439712468, -0.0, -0.0001688058439712468], [-0.0001688058439712468, -0.0, -0.0001688058439712468]], [[-0.00020160485068862791, -0.00020160485068862791, -0.00024174795233184815]]]
epoch over
tempforwardpass is
[0.978532093911783]
tempforwardpass is
[0.9

tempforwardpass is
[0.9786452645651987]
tempforwardpass is
[0.033477168653771455]
tempforwardpass is
[0.9956948066997967]
cost is
0.00010515805700961186
numiter is
6853
numwholedata pass is
1713
ioindex is 0
simulated deljtheata
[[[-0.00016569819226098403, 0.0, -0.00016569819226098403], [-0.00016569819226098403, 0.0, -0.00016569819226098403]], [[-0.00019796135771152075, -0.00019796135771152075, -0.00023729933103267304]]]
real deljtheta
deljtheta is
[[[-0.00016569819226098403, -0.0, -0.00016569819226098403], [-0.00016569819226098403, -0.0, -0.00016569819226098403]], [[-0.00019796135771152075, -0.00019796135771152075, -0.00023729933103267304]]]
epoch over
tempforwardpass is
[0.9786709284190126]
tempforwardpass is
[0.9786667871740898]
tempforwardpass is
[0.03349223746512088]
tempforwardpass is
[0.9956975890634441]
cost is
0.00010514216476225216
numiter is
6854
numwholedata pass is
1713
ioindex is 1
simulated deljtheata
[[[0.0, -0.00016508354173429987, -0.00016508354173429987], [0.0, -0.00

tempforwardpass is
[0.9957182621204081]
cost is
0.00010297221377302835
numiter is
6948
numwholedata pass is
1736
ioindex is 3
simulated deljtheata
[[[-0.00016322101022463943, 0.0, -0.00016322101022463943], [-0.00016322101022463943, 0.0, -0.00016322101022463943]], [[-0.00019502321479035345, -0.00019502321479035345, -0.00023371315240490673]]]
real deljtheta
deljtheta is
[[[-0.00016322101022463943, -0.0, -0.00016322101022463943], [-0.00016322101022463943, -0.0, -0.00016322101022463943]], [[-0.00019502321479035345, -0.00019502321479035345, -0.00023371315240490673]]]
epoch over
tempforwardpass is
[0.9787883685904355]
tempforwardpass is
[0.9787796257370567]
tempforwardpass is
[0.03322336442386517]
tempforwardpass is
[0.9957209877759863]
cost is
0.00010295647922013559
numiter is
6949
numwholedata pass is
1737
ioindex is 0
simulated deljtheata
[[[-0.00016272718992851661, 0.0, -0.00016272718992851661], [-0.00016272718992851661, 0.0, -0.00016272718992851661]], [[-0.0001944786482652907, -0.000194

simulated deljtheata
[[[-0.0001614139126349532, 0.0, -0.0001614139126349532], [-0.0001614139126349532, 0.0, -0.0001614139126349532]], [[-0.0001928949478874124, -0.0001928949478874124, -0.00023111273899845122]]]
real deljtheta
deljtheta is
[[[-0.0001614139126349532, -0.0, -0.0001614139126349532], [-0.0001614139126349532, -0.0, -0.0001614139126349532]], [[-0.0001928949478874124, -0.0001928949478874124, -0.00023111273899845122]]]
epoch over
tempforwardpass is
[0.978865861007684]
tempforwardpass is
[0.9788619314845417]
tempforwardpass is
[0.033022365478038905]
tempforwardpass is
[0.9957374698887169]
cost is
0.00010137168678544812
numiter is
7020
numwholedata pass is
1754
ioindex is 3
simulated deljtheata
[[[0.0, -0.00016082910260987492, -0.00016082910260987492], [0.0, -0.00016082910260987492, -0.00016082910260987492]], [[-0.00019226237110798918, -0.00019226237110798918, -0.0002303373574564395]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00016082910260987492, -0.00016082910260987492], [-0.0, 

In [ ]:
pow(10,-3)